# Séance 1 : Modéliser des flux protéiques dans la cellule grâce à l'algèbre linéaire

In [1]:
import numpy as np # numpy est la bibliothèque de calcul numérique en python. 

import matplotlib.pyplot as plt # Matplotlib permet de tracer des graphes.

# la commande jupyter ci-dessous permet d'afficher les graphes de matplotlib directement dans le notebook.
%matplotlib inline

from matplotlib.patches import Polygon # objet permettant de tracer des polygones

plt.rc('text', usetex=True) # Configure matplotlib pour utiliser TeX pour le rendu des textes 

# Une histoire de flux

Le transport des protéines dans la cellule eucaryote est un phénomène complexe faisant appel à  de nombreux compartiments (reticulum endoplasmique, noyau, appareil de Golgi, vésicules, mitochondries, plastes, membrane) et à des flux de matière très controlés qui les relient. 

On s'intéresse au suivi de protéines fluorescentes marquées à la GFP  dans la cellule. On souhaite décrire l'évolution de leur localisation dans les différents compartiments cellulaires, sachant que ces protéines marquées peuvent être transportées entre compartiments, ou dégradées, et que de nouvelles protéines peuvent être synthétisées.

Pour cela, nous proposons de réaliser un modèle linéaire en compartiments. 


### **Exercice 0:** 
Commençons en une dimension par considérer l'évolution de la quantité totale de protéines dans la cellule, $u(t)$. On suppose qu'à chaque pas de temps, cette quantité est multipliée par une constante $a$ (système linéaire - suite géométrique), tel que $$u(t+1)= a u(t)$$

Représenter la trajectoire pour $u(0)=1$ et a=1, a=1.15 ou a=0.95. Interpréter. 
(Indice : utiliser `plt.plot`).

#  Rappels sur les matrices

Une matrice $A$ de taille $m \times n$ à  coefficient dans $\mathbb C$ est un ensemble d'éléments de $\mathbb C$ ordonnés en $m$ lignes et $n$ colonnes.On note $a_{ij}$ l'élément à  la $i\text{-ème}$ ligne et $k\text{-ème}$ colonne.

\begin{equation} 
A = (a_{ij})_{1\leq i\leq m; 1 \leq j \leq n} 
\end{equation}

On peut aussi commencer l'indexation à  0 pour coller à  la représentation informatique: $A = (a_{ij})_{0 \leq i < m; 0 \leq j < n}$

Exemple en taille $3 \times 3$:

\begin{equation}
A = \left [ \begin{array}{ccc} a_{00} & a_{01} & a_{02} \\
                               a_{10} & a_{11} & a_{12} \\
                               a_{20} & a_{21} & a_{22} \\
                               \end{array} \right ] 
\end{equation}

In [2]:
# Les matrices peuvent être représentées par des objets de type numpy.array. 
# Créer un array peut se faire à  partir d'une liste de liste:
A = np.array([[10,6,6],
              [8,2,4],
              [8,4,2]])

# Accéder à  $a_{ij}$ se fait par indexation:
A[0,1] # => 6

# Il existe des constructeurs pour des matrices particulières:
I = np.identity(3) # Matrice identité de taille 3
N = np.zeros((3,3)) # Matrice de zeros de taille 3
X,Y = np.meshgrid([1,2,3],[1,2,3]) # Matrices donnant le produit cartésien de deux vecteurs (permet d'obtenir un maillage).

In [3]:
x = np.array([1,2,3])
# Le produit matriciel pour les np.array peut se faire avec la méthode .dot:
A.dot(x) # Seule possibilité pour Python < 3.5
# Ou l'opérateur @:
A @ x #Python >= 3.5
assert np.all(A.dot(x) ==  A @ x)

In [4]:
# Le produit matriciel n'est défini que pour des matrice de dimensions compatibles. 
# Exemple, le produit: A * B necessite que A ait autant de colonnes que B ait de lignes. 
# Le résultat est une matrice carrée. 
# (n,m) * (m,k) -> (n,k)

# Par défaut les array numpy de dimension 1 sont orientés à  chaque opération pour que le produit matriciel fonctionne :
x = np.array([1,2,3])
print("value: {}, dim: {}, shape: {}, A@x: {}, x@A {}".format(x, x.ndim, x.shape, A@x, x@A))

# Ainsi, Pour deux arrays de dimension 1, @ est le produit scalaire.
x@x # équivalent à  <x,x> ou x^T * x si x est un vecteur colonne.


value: [1 2 3], dim: 1, shape: (3,), A@x: [40 24 22], x@A [50 22 20]


14

In [5]:
# La syntaxe np.newaxis permet d'augmenter sa dimension. Maintenant, l'orientation ligne ou colonne est importante.
b = x[:,np.newaxis] # `b` est un vecteur colonne (3 lignes, 1 colonne)
print("value: {}, dim: {}, shape: {}, A@b: {}".format(b, b.ndim, b.shape, A@b))

c = x[np.newaxis,:] # `c` est un vecteur ligne (1 ligne, 3 colonnes)
print("value: {}, dim: {}, shape: {}, b@A:{}".format(c, c.ndim, c.shape, c@A))

c@b #=> un scalaire (produit scalaire des deux vecteurs <b,c>).
b@c #=> une matrice 3x3. 

value: [[1]
 [2]
 [3]], dim: 2, shape: (3, 1), A@b: [[40]
 [24]
 [22]]
value: [[1 2 3]], dim: 2, shape: (1, 3), b@A:[[50 22 20]]


array([[1, 2, 3],
       [2, 4, 6],
       [3, 6, 9]])

In [6]:
# NB : l'opérateur "*" avant un vecteur permet de "déballer" ses coordonées (nécessaire lorsque l'on veut plotter des vecteurs). 
x = [1.0, 0.1, 0.5]

print(*x)

1.0 0.1 0.5


# Partie 1 : Simuler des trajectoires

On considère le modèle simplifié suivant, où les transports sont représentés en vert, les synthèses en jaune et les dégradations en rouge :
 


svg image


### **Exercice 1** : 
Écrire la matrice $A$ qui décrit ce système dynamique linéaire $u_{t+1}=Au_t$, où $u_t$ est un vecteur indiquant les concentrations de protéines marquées à la GFP dans l'appareil de Golgi, les endosomes et la membrane plasmique respectivement. 

### **Exercice 2** : 
1) Écrire une fonction qui construit la matrice A tout en vérifiant la conservation de la matière.  (Indice : utiliser `assert`).

2) Simuler la trajectoire de ce modèle simplifié, pour f=0.4, m=0.2, r=0.5, e=0.4, g=0.1, s=0.5, et d=0. Tracer le graphe du contenu de chaque compartiment au cours du temps, sachant qu'au départ, la protéine est seulement présente en concentration 1 dans le Golgi. (Indice : utiliser `plt.subplots`).

3) Représenter différents types de trajectoires, en faisant varier le ratio synthèse/dégradation. (Indice : utiliser `plt.subplots`).







# Partie 2 : matrices $2\times 2$, des endomorphismes sur le plan

Pour encore simplifier et essayer de se construire une intuition géométrique on va passer à des matrices $2 \times 2$. 






\begin{equation}
A = \left [ \begin{array}{cc} a_{00} & a_{01} \\
                               a_{10} & a_{11}  \\
                               \end{array} \right ] 
\end{equation}

## Représenter l'effet d'une matrice



**Comment représenter une application en fonction de ses espaces de départ et d'arrivée**


| Espace de départ | Espace d'arrivée | Représentation graphique | Matplotlib |
|----------|----------|----------|----------|
|$\mathbb R$| $\mathbb R$ | courbe, points | `plt.plot`, `plt.scatter`|
|$\mathbb R^2$| $\mathbb R$ | contour, surface | `plt.contour`, `plt.contourf`, `plt.imshow`, [`axes3D.plot_surface`](https://matplotlib.org/mpl_toolkits/mplot3d/tutorial.html)|
|$\mathbb R^2$| $\mathbb R^2$ | champ de vecteur, écoulement | `plt.quiver`, `plt.streamplot` |






### **Exercice 3** : 
Soit la matrice \begin{equation}
A = \left [ \begin{array}{cc} 1.2 & 0.46 \\
                               0.45 & 0.8  \\
                               \end{array} \right ] 
\end{equation}


1) Représenter l'effet du produit matriciel sur différents vecteurs du plan. (Indice: utiliser les fonctions `plt.scatter` et `plt.arrow`. Options : `plt.set`, `plt.legend` et `plt.grid`). 

2) Illustrer la transformation en utilisant un champs de vecteur. (Indice: utiliser les fonctions `np.linspace`, `np.meshgrid`, `np.vectorize` et `plt.quiver`).

**NB:** `np.vectorize` permet de donner à une fonction quelconque des capacités de broadcasting (application à tous les éléments). Par défaut `np.vectorize` attend une fonction qui prend des scalaires et retourne des scalaires. Si ce n'est pas le cas il faut préciser la signature. par exemple, si la fonction prend deux scalaires et
 retourne un array de taille 2 : "(),()->(2)".

3) Représenter l'effet du produit matriciel sur le carré unité (i.e. carré formé à partir des vecteurs de la base canonique).  (Indice: utiliser la fonction `plt.add_patch(Polygon())`). Superposer un cercle unité (sachant que son équation correspond à $x^2+y^2=1$). 

4) Interpréter ces transformations en terme d'évolution du système Réticulum-Golgi.

## Produit Matriciel : Composer les transformations

**Multiplier des matrices** revient à  composer les transformations, c'est à  dire les appliquer les unes après les autres (en partant de la plus intérieure): $B \circ C$ revient à appliquer la transformation $C$, puis $B$.


### **Exercice 4** : 
Soient les matrices \begin{equation}
C = \left [ \begin{array}{cc} 1 & 1 \\
                               0 & 1  \\
                               \end{array} \right ] \text{ et }  R = \left [ \begin{array}{cc} 0 & -1 \\
                               1 & 0  \\
                               \end{array} \right ] 
                               \end{equation}
                               
1) De quels types de transformations s'agit-il ?

2) L'opération matricielle est-elle commutative dans ce cas ?

## Inverser une matrice : chercher la transformation inverse

**Inverser une matrice** revient à trouver la transformation qui annule la transformation associée à cette matrice. Si on garde en tête le fait que la multiplication est une composition des transformations (on en applique l'une puis l'autre) on comprend bien pourquoi: 
$$A^{-1}A = AA^{-1} = I$$ 




### **Exercice 5** : 

1) Inverser les matrices A, C et R. Répresenter ces transformations inverses sur le carré unité. (Indice : utiliser `np.linalg.inv`).

2) Soit la matrice \begin{equation} D(t) = \left [ \begin{array}{cc} cos(t) & 0 \\
                               sin(t) & 1  \\
                               \end{array} \right ]\end{equation}
                               
Regarder, pour plusieurs valeurs de t, les matrices D(t), leur inverse et leur déterminant, notamment quand le volume du carré unité passe par 0. Calculer la valeur du déterminant de chaque matrice. (Indice : utiliser `np.linalg.det`).

## Diagonaliser une matrice: Chercher la direction dans laquelle la transformation est une dilatation


   ### **Exercice 6** :  
   Diagonalisation :

1) Pour chacune des matrices suivantes, calculer les valeurs propres, répresenter la déformation du carré unité ainsi que les axes propres et vecteurs propres qui caractérisent ces transformations. (Indice : utiliser `np.linalg.eig`).


\begin{equation}
 I = \left [ \begin{array}{cc} 2 & 0 \\
                               0 & 1  \\
                               \end{array} \right ] ,  J = \left [ \begin{array}{cc} 1 & 0 \\
                               0 & 0.5  \\
                               \end{array} \right ] ,  K = \left [ \begin{array}{cc} 2 & 0 \\
                               0 & 0  \\
                               \end{array} \right ] ,  L = \left [ \begin{array}{cc} 2 & 0 \\
                               0 & -1  \\
                               \end{array} \right ] \text{ et  }  M = \left [ \begin{array}{cc} -1 & 0 \\
                               0 & -2  \\
                               \end{array} \right ] 
                               \end{equation}
                    
   
                    
\begin{equation}
A = \left [ \begin{array}{cc} 1.2 & 0.46 \\
                               0.45 & 0.8  \\
                               \end{array} \right ], B = \left [ \begin{array}{cc} 0.55 & 0.46 \\
                               0.45 & 0.5  \\
                               \end{array} \right ],  \text{ et  } C = \left [ \begin{array}{cc} 0 & 0.9  \\
                               1  & 0   \\
                               \end{array} \right ]
                               \end{equation}


2) Superposer des trajectoires sur ces représentations, en proposant plusieurs conditions initiales. 


3) Interpréter, si possible, ces transformations en terme d'évolution du système Réticulum-Golgi.


## Perron-Frobenius


### **Exercice 7** : 
Appliquer Perron-Frobenius


1) Pour chacune des matrices suivantes, calculer les valeurs propres, répresenter la déformation du carré unité ainsi que les axes propres et vecteurs propres qui caractérisent ces transformations. 

        
\begin{equation}
A = \left [ \begin{array}{cc} 1.2 & 0.46 \\
                               0.45 & 0.8  \\
                               \end{array} \right ], B = \left [ \begin{array}{cc} 0.55 & 0.46 \\
                               0.45 & 0.5  \\
                               \end{array} \right ],  C = \left [ \begin{array}{cc} cos(\pi/4) & -sin(\pi/4) \\
                               sin(\pi/4) & cos(\pi/4)  \\
                               \end{array} \right ],  D = \left [ \begin{array}{cc} 0 & -0.95 \\
                               0.95 & 0  \\
                               \end{array} \right ],  E = \left [ \begin{array}{cc} 0 & -1.05 \\
                               1.05 & 0  \\
                               \end{array} \right ],
                               F = \left [ \begin{array}{cc} 0 & 1 \\
                               1.1 & 1.2  \\
                               \end{array} \right ],  G = \left [ \begin{array}{cc} 1 & 1 \\
                               0 & 1  \\
                               \end{array} \right ],  H = \left [ \begin{array}{cc} 0 & 1 \\
                               1 & 0  \\
                               \end{array} \right ], \text{ et  } I = \left [ \begin{array}{cc} 0 & 1.05 \\
                               1.06 & 0  \\
                               \end{array} \right ] 
                               \end{equation}
                               

2) Quelles matrices sont positives ? Régulières ? Appliquer Perron-Frobenius.


3) Superposer des trajectoires sur ces représentations, en proposant plusieurs conditions initiales.


4) Interpréter, si possible, ces transformations en terme d'évolution du système Réticulum-Golgi.





# Partie 3 : Inférence


### **Exercice 8 :**

Une protéine marquée à la GFP est suivie au cours du temps dans les cellules pancréatiques et les concentrations suivantes ont été mesurées dans le Reticulum et le Golgi. 



| temps | départ | 5 minutes | 10 minutes | 15 minutes | 20 minutes |
|----------|----------|----------|----------|----------|----------|
| Reticulum | 1.0 | 1.2 | 1.3 | 1.4 | 1.6 |
| Golgi | 0.0 | 0.3 | 0.5 | 0.7 | 0.8 |

1) Modéliser ce flux protéique à l'aide d'un modèle linéaire. En utilisant la méthode des moindres carrés, estimer les valeurs des paramètres du modèle linéaire décrivant le mieux le comportement du système. 

2) Quelles concentrations prédisez-vous 40 minutes après le début de l'expérience ? Après 5 heures ?

